## Testing Cuda

In [2]:
# Now verify our GPU setup
import torch

print("PyTorch version:", torch.__version__)
print("CUDA available:", torch.cuda.is_available())
if torch.cuda.is_available():
    print("CUDA version:", torch.version.cuda)
    print("GPU device name:", torch.cuda.get_device_name(0))
    print("GPU memory allocated:", torch.cuda.memory_allocated(0)/1024**2, "MB")
    print("GPU memory reserved:", torch.cuda.memory_reserved(0)/1024**2, "MB")

PyTorch version: 2.6.0+cu126
CUDA available: True
CUDA version: 12.6
GPU device name: NVIDIA GeForce RTX 3060
GPU memory allocated: 0.0 MB
GPU memory reserved: 0.0 MB


## Load Dataset

In [3]:
import pandas as pd
from datasets import Dataset, DatasetDict
import os

def load_urdu_dataset(data_dir):
    """
    Load Urdu dataset from local TSV files
    data_dir: Directory containing train.tsv, dev.tsv, test.tsv and clips folder
    """
    # Load TSV files
    train_df = pd.read_csv(os.path.join(data_dir, 'train.tsv'), sep='\t')
    dev_df = pd.read_csv(os.path.join(data_dir, 'dev.tsv'), sep='\t')
    test_df = pd.read_csv(os.path.join(data_dir, 'test.tsv'), sep='\t')
    
    # Add full audio path
    clips_dir = os.path.join(data_dir, 'clips')
    train_df['audio'] = train_df['path'].apply(lambda x: os.path.join(clips_dir, x))
    dev_df['audio'] = dev_df['path'].apply(lambda x: os.path.join(clips_dir, x))
    test_df['audio'] = test_df['path'].apply(lambda x: os.path.join(clips_dir, x))
    
    # Keep only necessary columns
    columns_to_keep = ['audio', 'sentence']
    train_df = train_df[columns_to_keep]
    dev_df = dev_df[columns_to_keep]
    test_df = test_df[columns_to_keep]
    
    # Convert to Hugging Face datasets
    train_dataset = Dataset.from_pandas(train_df)
    dev_dataset = Dataset.from_pandas(dev_df)
    test_dataset = Dataset.from_pandas(test_df)
    
    # Combine into DatasetDict
    dataset_dict = DatasetDict({
        'train': train_dataset,
        'validation': dev_dataset,
        'test': test_dataset
    })
    
    return dataset_dict

# Load the dataset
# Replace with your actual data directory path
data_dir = "S:/cv-corpus-20.0-2024-12-06/ur"
urdu_dataset = load_urdu_dataset(data_dir)

# Print dataset statistics
print("\nDataset statistics:")
for split in urdu_dataset:
    print(f"{split}: {len(urdu_dataset[split])} examples")

# Print first example from training set
print("\nExample from training set:")
print(urdu_dataset['train'][0])


Dataset statistics:
train: 7205 examples
validation: 4982 examples
test: 5026 examples

Example from training set:
{'audio': 'S:/cv-corpus-20.0-2024-12-06/ur\\clips\\common_voice_ur_31898340.mp3', 'sentence': 'طرح طرح کے پرندے'}


In [4]:
urdu_dataset

DatasetDict({
    train: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 7205
    })
    validation: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 4982
    })
    test: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 5026
    })
})

## Prepare Feature Extractor, Tokenizer and Data

In [5]:
from transformers import WhisperFeatureExtractor, WhisperTokenizer, WhisperProcessor

# Initialize the feature extractor
feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-small")

# Initialize the tokenizer with Urdu language
tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-small", language="Urdu", task="transcribe")

# Let's also create the processor which combines both feature_extractor and tokenizer
processor = WhisperProcessor.from_pretrained("openai/whisper-small", language="Urdu", task="transcribe")

# Let's test the tokenizer with a sample Urdu text from our dataset
sample_text = urdu_dataset["train"][0]["sentence"]
print("\nTesting tokenizer:")
print("Original text:", sample_text)
encoded = tokenizer(sample_text)
print("Encoded text:", encoded)

decoded = tokenizer.decode(encoded.input_ids)
print("Decoded text:", decoded)

# Let's also look at the feature extractor's configuration
print("\nFeature extractor config:")
print("Sampling rate:", feature_extractor.sampling_rate)
print("Feature size:", feature_extractor.feature_size)
print("Padding value:", feature_extractor.padding_value)

preprocessor_config.json:   0%|          | 0.00/185k [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/283k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/836k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.48M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/494k [00:00<?, ?B/s]

normalizer.json:   0%|          | 0.00/52.7k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/34.6k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.19k [00:00<?, ?B/s]


Testing tokenizer:
Original text: طرح طرح کے پرندے
Encoded text: {'input_ids': [50258, 50290, 50359, 50363, 9566, 2288, 5016, 23032, 2288, 5016, 24049, 21453, 2288, 41260, 7369, 50257], 'attention_mask': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]}
Decoded text: <|startoftranscript|><|ur|><|transcribe|><|notimestamps|>طرح طرح کے پرندے<|endoftext|>

Feature extractor config:
Sampling rate: 16000
Feature size: 80
Padding value: 0.0


## Testing tokenizer

In [6]:
# Test tokenizer with and without special tokens
input_str = urdu_dataset["train"][0]["sentence"]
labels = tokenizer(input_str).input_ids
decoded_with_special = tokenizer.decode(labels, skip_special_tokens=False)
decoded_str = tokenizer.decode(labels, skip_special_tokens=True)

print("\nTokenizer test with special tokens:")
print(f"Input:                 {input_str}")
print(f"Decoded w/ special:    {decoded_with_special}")
print(f"Decoded w/out special: {decoded_str}")
print(f"Are equal:             {input_str == decoded_str}")


Tokenizer test with special tokens:
Input:                 طرح طرح کے پرندے
Decoded w/ special:    <|startoftranscript|><|ur|><|transcribe|><|notimestamps|>طرح طرح کے پرندے<|endoftext|>
Decoded w/out special: طرح طرح کے پرندے
Are equal:             True


## check default sampling rate of 1st training example

In [7]:
print(urdu_dataset["train"][0])

{'audio': 'S:/cv-corpus-20.0-2024-12-06/ur\\clips\\common_voice_ur_31898340.mp3', 'sentence': 'طرح طرح کے پرندے'}


## fixing sampling rate

In [8]:
# Now let's prepare our dataset with the correct sampling rate
# First, let's check the current audio format
from datasets import Audio
import numpy as np

# Cast the audio column to audio format
urdu_dataset = urdu_dataset.cast_column("audio", Audio(sampling_rate=16000))

# Let's examine the first audio file after casting
print("\nAudio format check:")
print("First example audio details:")
audio = urdu_dataset["train"][0]["audio"]
print(f"Path: {audio['path']}")
print(f"Sampling rate: {audio['sampling_rate']}")
print(f"Array shape: {audio['array'].shape}")


Audio format check:
First example audio details:
Path: S:/cv-corpus-20.0-2024-12-06/ur\clips\common_voice_ur_31898340.mp3
Sampling rate: 16000
Array shape: (50688,)


In [9]:
#check the format of 1st training example
print(urdu_dataset["train"][0])


{'audio': {'path': 'S:/cv-corpus-20.0-2024-12-06/ur\\clips\\common_voice_ur_31898340.mp3', 'array': array([1.39698386e-09, 1.74622983e-09, 2.91038305e-10, ...,
       1.17505246e-04, 1.56884955e-04, 4.67942300e-05]), 'sampling_rate': 16000}, 'sentence': 'طرح طرح کے پرندے'}


In [10]:
def prepare_dataset(batch, processor):
    """
    Prepare the dataset for training:
    1. Load and resample audio (already at 16kHz)
    2. Compute log-Mel input features
    3. Encode target text to label ids
    """
    # Load audio
    audio = batch["audio"]
    
    # Compute log-Mel input features using processor
    batch["input_features"] = processor.feature_extractor(
        audio["array"], 
        sampling_rate=audio["sampling_rate"]
    ).input_features[0]
    
    # Encode target text to label ids using processor
    batch["labels"] = processor.tokenizer(batch["sentence"]).input_ids
    return batch

In [11]:
# Process the entire dataset
print("\nProcessing the entire dataset...")
urdu_dataset = urdu_dataset.map(
    function=prepare_dataset,
    fn_kwargs={"processor": processor},  # Pass processor as a keyword argument
    remove_columns=urdu_dataset.column_names["train"],
    desc="Processing audio files",
    num_proc=1  # Adjust based on your CPU cores
)


Processing the entire dataset...


Processing audio files:   0%|          | 0/7205 [00:00<?, ? examples/s]

Processing audio files:   0%|          | 0/4982 [00:00<?, ? examples/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (8657 > 1024). Running this sequence through the model will result in indexing errors


ArrowMemoryError: realloc of size 8589934592 failed

In [12]:
# Create cache directory if it doesn't exist
import os
os.makedirs("./cached_dataset_small", exist_ok=True)

# Process the dataset with memory-efficient settings
print("\nProcessing the entire dataset...")
urdu_dataset = urdu_dataset.map(
    function=prepare_dataset,
    fn_kwargs={"processor": processor},
    remove_columns=urdu_dataset.column_names["train"],
    desc="Processing audio files",
    num_proc=1,  # Single process to avoid memory fragmentation
    batch_size=8,  # Process smaller batches
    batched=True,  # Enable batch processing
    writer_batch_size=100,  # Control memory during writing
    load_from_cache_file=True,  # Enable caching
    cache_file_names={  # Note: cache_file_names instead of cache_file_name
        "train": "./cached_dataset_small/train_cache",
        "validation": "./cached_dataset_small/validation_cache",
        "test": "./cached_dataset_small/test_cache"
    }
)


Processing the entire dataset...


Processing audio files:   0%|          | 0/7205 [00:00<?, ? examples/s]

Processing audio files:   0%|          | 0/4982 [00:00<?, ? examples/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (8657 > 1024). Running this sequence through the model will result in indexing errors


Processing audio files:   0%|          | 0/5026 [00:00<?, ? examples/s]

In [ ]:

# Save the processed dataset locally
output_dir = "processed_urdu_dataset"
urdu_dataset.save_to_disk(output_dir)
print(f"\nDataset saved to: {output_dir}")

# To verify the save worked, let's load a small part of it
print("\nVerifying saved dataset:")
from datasets import load_from_disk

# Load just one example to verify
loaded_dataset = load_from_disk(output_dir)
print("\nFirst example from saved dataset:")
print("Input features shape:", loaded_dataset["train"][0]["input_features"].shape)
print("Labels length:", len(loaded_dataset["train"][0]["labels"]))

In [13]:
# Print the first example from processed dataset
print("\nFirst example from processed dataset:")
print(urdu_dataset["train"][0])


First example from processed dataset:
{'input_features': [[-0.5100164413452148, -0.5100164413452148, -0.5100164413452148, -0.5100164413452148, -0.21474695205688477, -0.07383286952972412, 0.09040546417236328, -0.2061218023300171, 0.2822064757347107, 0.33895450830459595, 0.32921290397644043, 0.46163612604141235, 0.5057690143585205, 0.4573923349380493, 0.507580041885376, 0.5383383631706238, 0.4349222779273987, 0.2459014654159546, 0.25031495094299316, 0.08782994747161865, -0.17286062240600586, 0.23453831672668457, -0.2927652597427368, -0.03643798828125, 0.08821761608123779, 0.07298803329467773, 0.06279486417770386, -0.09528100490570068, -0.07303941249847412, 0.2062091827392578, 0.10648727416992188, 0.041926801204681396, 0.10808855295181274, 0.2051142454147339, -0.13070666790008545, -0.11405158042907715, -0.26921868324279785, 0.08697313070297241, -0.14893388748168945, -0.17748796939849854, -0.019710421562194824, 0.11173290014266968, 0.29822874069213867, 0.28273189067840576, 0.3363326191902

In [14]:

# Print dataset format
print("\nDataset format:")
print(urdu_dataset)


Dataset format:
DatasetDict({
    train: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 7205
    })
    validation: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 4982
    })
    test: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 5026
    })
})


In [18]:
from huggingface_hub import login
# Login to Hugging Face (you'll be prompted for your token)
login()

In [21]:
# # Push the dataset to the Hub
# dataset_name = "urdu-common-voice-20-processed-large-v3"
# urdu_dataset.push_to_hub(
#     f"osman31/{dataset_name}",
#     private=True  # Set to False if you want it public
# )

# print(f"Dataset pushed to: https://huggingface.co/datasets/osman31/{dataset_name}")

Uploading the dataset shards:   0%|          | 0/23 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

...

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Dataset pushed to: https://huggingface.co/datasets/osman31/urdu-common-voice-20-processed-large-v3


# Step 2 - Training